# Email Associations Analysis

This notebook analyzes email associations in HubSpot tickets and compares ticket content with their first associations.

In [4]:
import os
import pandas as pd
import requests
from datetime import datetime
import time
from tqdm import tqdm
import json
from dotenv import load_dotenv

# Load environment variables
load_dotenv()

# Get HubSpot API key
HUBSPOT_API_KEY = os.getenv('HUBSPOT_API_KEY')
if not HUBSPOT_API_KEY:
    raise ValueError("HUBSPOT_API_KEY not found in environment variables")

# API endpoints
BASE_URL = "https://api.hubapi.com"
TICKETS_ENDPOINT = f"{BASE_URL}/crm/v3/objects/tickets"
ASSOCIATIONS_ENDPOINT = f"{BASE_URL}/crm/v3/objects/tickets/associations/emails"
EMAILS_ENDPOINT = f"{BASE_URL}/crm/v3/objects/emails"

# Headers for API requests
headers = {
    "Authorization": f"Bearer {HUBSPOT_API_KEY}",
    "Content-Type": "application/json",
    "Accept": "application/json"
}

In [5]:
def get_tickets(batch_size=100, after=None):
    """Fetch tickets from HubSpot with pagination"""
    params = {
        "limit": batch_size,
        "properties": ["hs_ticket_id", "subject", "hs_ticket_priority", "createdate", "hs_pipeline", "hs_pipeline_stage"],
        "archived": False
    }
    
    if after:
        params["after"] = after
    
    response = requests.get(TICKETS_ENDPOINT, headers=headers, params=params)
    response.raise_for_status()
    return response.json()

def get_email_associations(ticket_id):
    """Fetch email associations for a specific ticket"""
    params = {
        "limit": 100,
        "archived": False
    }
    
    url = f"{ASSOCIATIONS_ENDPOINT}/{ticket_id}/to/email"
    response = requests.get(url, headers=headers, params=params)
    response.raise_for_status()
    return response.json()

def get_email_details(email_id):
    """Fetch details of a specific email"""
    url = f"{EMAILS_ENDPOINT}/{email_id}"
    response = requests.get(url, headers=headers)
    response.raise_for_status()
    return response.json()

In [6]:
# Fetch all tickets
all_tickets = []
after = None

while True:
    try:
        response = get_tickets(after=after)
        tickets = response.get('results', [])
        all_tickets.extend(tickets)
        
        # Check if there are more pages
        paging = response.get('paging', {})
        next_page = paging.get('next', {}).get('after')
        
        if not next_page:
            break
            
        after = next_page
        time.sleep(0.1)  # Rate limiting
        
    except Exception as e:
        print(f"Error fetching tickets: {e}")
        break

print(f"Total tickets fetched: {len(all_tickets)}")

Total tickets fetched: 32403


In [7]:
# Create DataFrame from tickets
tickets_df = pd.DataFrame(all_tickets)
tickets_df['id'] = tickets_df['id'].astype(str)
tickets_df.head()

id                                         properties  \
0  1103130093  {'createdate': '2023-03-08T09:31:21.271Z', 'hs...   
1  1103599809  {'createdate': '2023-03-08T13:02:22.688Z', 'hs...   
2  1103646927  {'createdate': '2023-03-08T13:26:58.484Z', 'hs...   
3  1103824108  {'createdate': '2023-03-08T15:05:49.854Z', 'hs...   
4  1103982270  {'createdate': '2023-03-08T16:13:59.401Z', 'hs...   

                  createdAt                 updatedAt  archived  
0  2023-03-08T09:31:21.271Z  2024-05-21T20:38:04.101Z     False  
1  2023-03-08T13:02:22.688Z  2024-08-27T10:44:09.802Z     False  
2  2023-03-08T13:26:58.484Z  2024-12-26T15:51:26.592Z     False  
3  2023-03-08T15:05:49.854Z  2024-09-10T08:33:00.626Z     False  
4  2023-03-08T16:13:59.401Z  2025-02-17T13:23:02.519Z     False

In [8]:
# Fetch email associations for each ticket
ticket_associations = []

for ticket_id in tqdm(tickets_df['id']):
    try:
        associations = get_email_associations(ticket_id)
        results = associations.get('results', [])
        
        for assoc in results:
            ticket_associations.append({
                'ticket_id': ticket_id,
                'association_id': assoc.get('id'),
                'association_type': assoc.get('associationTypeId'),
                'association_category': assoc.get('associationCategory')
            })
        
        time.sleep(0.1)  # Rate limiting
        
    except Exception as e:
        print(f"Error fetching associations for ticket {ticket_id}: {e}")
        continue

# Create DataFrame from associations
associations_df = pd.DataFrame(ticket_associations)
associations_df.head()

  0%|                                                           | 2/32403 [00:00<1:34:47,  5.70it/s]

Error fetching associations for ticket 1103130093: 404 Client Error: Not Found for url: https://api.hubapi.com/crm/v3/objects/tickets/associations/emails/1103130093/to/email?limit=100&archived=False
Error fetching associations for ticket 1103599809: 404 Client Error: Not Found for url: https://api.hubapi.com/crm/v3/objects/tickets/associations/emails/1103599809/to/email?limit=100&archived=False


  0%|                                                           | 5/32403 [00:00<1:04:32,  8.37it/s]

Error fetching associations for ticket 1103646927: 404 Client Error: Not Found for url: https://api.hubapi.com/crm/v3/objects/tickets/associations/emails/1103646927/to/email?limit=100&archived=False
Error fetching associations for ticket 1103824108: 404 Client Error: Not Found for url: https://api.hubapi.com/crm/v3/objects/tickets/associations/emails/1103824108/to/email?limit=100&archived=False
Error fetching associations for ticket 1103982270: 404 Client Error: Not Found for url: https://api.hubapi.com/crm/v3/objects/tickets/associations/emails/1103982270/to/email?limit=100&archived=False


  0%|                                                             | 7/32403 [00:00<57:46,  9.34it/s]

...

100%|█████████████████████████████████████████████████████▉| 32363/32403 [1:05:37<00:00, 355.80it/s]

Error fetching associations for ticket 105128439020: HTTPSConnectionPool(host='api.hubapi.com', port=443): Max retries exceeded with url: /crm/v3/objects/tickets/associations/emails/105128439020/to/email?limit=100&archived=False (Caused by NameResolutionError("<urllib3.connection.HTTPSConnection object at 0x0000018DB2A49290>: Failed to resolve 'api.hubapi.com' ([Errno 11001] getaddrinfo failed)"))
Error fetching associations for ticket 105128439033: HTTPSConnectionPool(host='api.hubapi.com', port=443): Max retries exceeded with url: /crm/v3/objects/tickets/associations/emails/105128439033/to/email?limit=100&archived=False (Caused by NameResolutionError("<urllib3.connection.HTTPSConnection object at 0x0000018DB2A3E490>: Failed to resolve 'api.hubapi.com' ([Errno 11001] getaddrinfo failed)"))
Error fetching associations for ticket 105128449239: HTTPSConnectionPool(host='api.hubapi.com', port=443): Max retries exceeded with url: /crm/v3/objects/tickets/associations/emails/105128449239/to/

100%|███████████████████████████████████████████████████████| 32403/32403 [1:05:37<00:00,  8.23it/s]


Error fetching associations for ticket 107141915868: HTTPSConnectionPool(host='api.hubapi.com', port=443): Max retries exceeded with url: /crm/v3/objects/tickets/associations/emails/107141915868/to/email?limit=100&archived=False (Caused by NameResolutionError("<urllib3.connection.HTTPSConnection object at 0x0000018DB2A445D0>: Failed to resolve 'api.hubapi.com' ([Errno 11001] getaddrinfo failed)"))
Error fetching associations for ticket 107152843965: HTTPSConnectionPool(host='api.hubapi.com', port=443): Max retries exceeded with url: /crm/v3/objects/tickets/associations/emails/107152843965/to/email?limit=100&archived=False (Caused by NameResolutionError("<urllib3.connection.HTTPSConnection object at 0x0000018DB1719CD0>: Failed to resolve 'api.hubapi.com' ([Errno 11001] getaddrinfo failed)"))
Error fetching associations for ticket 107185022150: HTTPSConnectionPool(host='api.hubapi.com', port=443): Max retries exceeded with url: /crm/v3/objects/tickets/associations/emails/107185022150/to/

Empty DataFrame
Columns: []
Index: []

In [9]:
# Merge tickets and associations
merged_df = pd.merge(tickets_df, associations_df, left_on='id', right_on='ticket_id', how='left')
merged_df.head()

KeyError: 'ticket_id'

In [ ]:
# Analysis of null association IDs
null_associations = merged_df[merged_df['association_id'].isna()]
print(f"Total tickets with null associations: {len(null_associations)}")
print(f"Percentage of tickets with null associations: {(len(null_associations) / len(tickets_df)) * 100:.2f}%")

# Group by ticket to see how many associations each ticket has
association_counts = merged_df.groupby('ticket_id')['association_id'].count().reset_index()
print("\nAssociation count distribution:")
print(association_counts['association_id'].value_counts().sort_index())

In [ ]:
# Function to compare ticket content with first association
def compare_ticket_with_first_association(ticket_id):
    try:
        # Get ticket details
        ticket = tickets_df[tickets_df['id'] == ticket_id].iloc[0]
        
        # Get first association
        associations = get_email_associations(ticket_id)
        if not associations.get('results'):
            return None
            
        first_assoc = associations['results'][0]
        email_id = first_assoc.get('id')
        
        # Get email details
        email = get_email_details(email_id)
        
        return {
            'ticket_id': ticket_id,
            'ticket_subject': ticket.get('properties', {}).get('subject'),
            'email_subject': email.get('properties', {}).get('hs_email_subject'),
            'email_text': email.get('properties', {}).get('hs_email_text'),
            'email_html': email.get('properties', {}).get('hs_email_html')
        }
    except Exception as e:
        print(f"Error comparing ticket {ticket_id}: {e}")
        return None

In [ ]:
# Compare a sample of tickets with their first associations
sample_size = 100
sample_tickets = tickets_df['id'].sample(n=sample_size)
comparison_results = []

for ticket_id in tqdm(sample_tickets):
    result = compare_ticket_with_first_association(ticket_id)
    if result:
        comparison_results.append(result)
    time.sleep(0.1)  # Rate limiting

# Create DataFrame from comparison results
comparison_df = pd.DataFrame(comparison_results)
comparison_df.head()

In [ ]:
# Analyze subject matching
subject_matches = comparison_df['ticket_subject'] == comparison_df['email_subject']
match_percentage = (subject_matches.sum() / len(comparison_df)) * 100
print(f"Percentage of matching subjects: {match_percentage:.2f}%")

# Display examples of matches and mismatches
print("\nExample matches:")
print(comparison_df[subject_matches][['ticket_subject', 'email_subject']].head())
print("\nExample mismatches:")
print(comparison_df[~subject_matches][['ticket_subject', 'email_subject']].head())